# Locating a new art gallery in Los Angeles, California

# by Stuart Shim for the Applied Data Science Capstone Project for IBM

## Los Angeles Introduction and Overview

Los Angeles, California is known as the entertainment capital of the world. Movie and television studios including Paramount Pictures, Universal Studios, Warner Brothers, and Sony Pictures Entertainment are located in the Los Angeles basin. In the last decade, Los Angeles, has emerged as a major center for artists, collectors, art institutions, auction houses and galleries. Unlike most heavily-populated metropolitan areas in the world, Los Angeles, with a current population of 4 million residents, and the second largest city in the United States, does not have a true center or downtown. Although recent major real estate developments may challenge this notion, Los Angeles has various centers of activity and business. In order to create a sense of community, various neighborhoods have been labeled with physical street signs informing those interested, that they are in a new or specific neighborhood. This idea is fairly common throughout the United States, and can be often seen in historic or architecturally significant neighborhoods. In Los Angeles, it's more a marketing and promotion effort for residents and real estate development. It has also resulted in greater fragmentation of existing or older neighborhoods.

## The Unique Geographic and Transportation Challenges of Los Angeles

There have been many theories and urban studies proffered to explain this phenomenon of no centralized business district in Los Angeles. But, the most likely explanation is the development of freeways in the Southern California region in the 1940s-70s. This freeway system encouraged decentralized home and commercial development. The good citizens of Southern California have paid the price for this development by having some of the worst traffic and air quality issues in North America. Travel times are much greater during peak traffic periods, so locating any business takes on greater importance in Los Angeles. Ask anyone who has flown into Los Angeles International Airport, how long it takes to travel the 19 miles to downtown Los Angeles. You may be surprised that the range can be from 24 minutes to 2+ hours, by car, depending on arrival time and traffic conditions.

## Business Problem

Because of the issues outlined previously, a burgeoning art market, a non-central business district or city core, and traffic, locating a new art gallery in Los Angeles takes on greater importance than other metropolitan areas in the United States. This project will examine and address this challenge.

## Target Audience

The target audience for this project includes: Entrepreneurs who have yet to launch an art gallery in Los Angeles, existing gallery owners who are considering expanding or relocating their operations, collectors interested in new venues to explore, art gallery suppliers, artists seeking new or additional representation, and art-loving visitors and tourists to Los Angeles.

## Project Methodology and Data Sources

The general methodology for this project will consist of transforming available neighborhood data from Wikipedia into various data frames, visualizing the locations of these neighborhoods, merging the neighborhood data with existing art gallery geolocation data provided by Foursquare, and then utilizing k-means clustering of neighborhoods to identify potential new locations for an art gallery. 
Web scraping the Wikipedia website and using Foursquare geolocation data will be employed extensively for this project. 

### Import libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files
!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
import re # allows Python to utililize regular expressions
import folium # map rendering library

print("Libraries and dependencies imported.")

Solving environment: ...working... done

# All requested packages already installed.

Libraries and dependencies imported.


### Scraping data from Wikipedia for districts and neighborhoods in Los Angeles

In [2]:
# send the GET request to Wikipedia
data = requests.get("https://en.wikipedia.org/wiki/List_of_districts_and_neighborhoods_of_Los_Angeles").text

In [3]:
# parse data from the html into a beautifulsoup object
soup1 = BeautifulSoup(data, 'html.parser')

In [4]:
# create a list to store neighborhood data
neighborhoodList = []

In [5]:
# taking a look at the data scraped from Wikipedia
soup1


<!DOCTYPE html>

<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of districts and neighborhoods of Los Angeles - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"a570e793-f43e-4690-9f9c-1d606847657f","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_districts_and_neighborhoods_of_Los_Angeles","wgTitle":"List of districts and neighborhoods of Los Angeles","wgCurRevisionId":959285729,"wgRevisionId":959285729,"wgArticleId":1647580,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["All articles with unsourced statements","Articles with u

In [6]:
# append/wrangle the data to a new list and eliminate any unnecessary data

for link in soup1.findAll('a', attrs={'href': re.compile("^/wiki/*,_Los_Angeles")}):
    print (link.get('href'))




for link in soup1.findAll('a', attrs={'href': re.compile("^/wiki/")}):
    print (link.get('title'))
    neighborhoodList.append(link.get('title'))

neighborhoodList = neighborhoodList[1:-85]


Los Angeles
Angelino Heights, Los Angeles
Angeles Mesa, Los Angeles
Angelus Vista, Los Angeles
Arleta, Los Angeles
Arlington Heights, Los Angeles
Arts District, Los Angeles
Atwater Village, Los Angeles
Baldwin Hills, Los Angeles
Baldwin Hills/Crenshaw, Los Angeles
Baldwin Village, Los Angeles
Baldwin Vista, Los Angeles
Beachwood Canyon, Los Angeles
Bel Air, Los Angeles
Benedict Canyon, Los Angeles
Beverly Crest, Los Angeles
Beverly Glen, Los Angeles
Beverly Grove, Los Angeles
Beverly Hills Post Office
Beverly Park, Los Angeles
Beverlywood, Los Angeles
Boyle Heights, Los Angeles
Brentwood, Los Angeles
Brentwood Circle, Los Angeles
Brentwood Glen, Los Angeles
Broadway-Manchester, Los Angeles
Brookside, Los Angeles
Bunker Hill, Los Angeles
Cahuenga Pass
Canoga Park, Los Angeles
Harvard Park, Los Angeles
Carthay, Los Angeles
Castle Heights, Los Angeles
Central-Alameda, Los Angeles
Downtown Los Angeles
Century City, Los Angeles
Chatsworth, Los Angeles
Chesterfield Square, Los Angeles
Chevio

In [7]:
# create a new DataFrame from the list
la_df = pd.DataFrame({"Neighborhood": neighborhoodList})

la_df.head()

Neighborhood
0   Angelino Heights, Los Angeles
1       Angeles Mesa, Los Angeles
2      Angelus Vista, Los Angeles
3             Arleta, Los Angeles
4  Arlington Heights, Los Angeles

In [8]:
la_df

Neighborhood
0          Angelino Heights, Los Angeles
1              Angeles Mesa, Los Angeles
2             Angelus Vista, Los Angeles
3                    Arleta, Los Angeles
4         Arlington Heights, Los Angeles
5             Arts District, Los Angeles
6           Atwater Village, Los Angeles
7             Baldwin Hills, Los Angeles
8    Baldwin Hills/Crenshaw, Los Angeles
9           Baldwin Village, Los Angeles
10            Baldwin Vista, Los Angeles
11         Beachwood Canyon, Los Angeles
12                  Bel Air, Los Angeles
13          Benedict Canyon, Los Angeles
14            Beverly Crest, Los Angeles
15             Beverly Glen, Los Angeles
16            Beverly Grove, Los Angeles
17             Beverly Hills Post Office
18             Beverly Park, Los Angeles
19              Beverlywood, Los Angeles
20            Boyle Heights, Los Angeles
21                Brentwood, Los Angeles
22         Brentwood Circle, Los Angeles
23           Brentwood Glen, Los Angeles
24      Broadway-Manchester, Los Angeles
25                Brookside, Los Angeles
26              Bunker Hill, Los Angeles
27                         Cahuenga Pass
28              Canoga Park, Los Angeles
29             Harvard Park, Los Angeles
30                  Carthay, Los Angeles
31           Castle Heights, Los Angeles
32          Central-Alameda, Los Angeles
33                  Downtown Los Angeles
34             Century City, Los Angeles
35               Chatsworth, Los Angeles
36      Chesterfield Square, Los Angeles
37            Cheviot Hills, Los Angeles
38                Chinatown, Los Angeles
39             Civic Center, Los Angeles
40                 Crenshaw, Los Angeles
41          Crestwood Hills, Los Angeles
42             Cypress Park, Los Angeles
43                  Del Rey, Los Angeles
44                  Downtown Los Angeles
45               Eagle Rock, Los Angeles
46        East Gate Bel Air, Los Angeles
47             Wikipedia:Citation needed
48           East Hollywood, Los Angeles
49          East Los Angeles, California
50                Echo Park, Los Angeles
51                 Edendale, Los Angeles
52                El Sereno, Los Angeles
53          Elysian Heights, Los Angeles
54             Elysian Park, Los Angeles
55           Elysian Valley, Los Angeles
56                   Encino, Los Angeles
57          Exposition Park, Los Angeles
58        Faircrest Heights, Los Angeles
59         Fairfax District, Los Angeles
60         Fashion District, Los Angeles
61    Historic Filipinotown, Los Angeles
62       Financial District, Los Angeles
63                 Florence, Los Angeles
64           Los Angeles Flower District
65           Franklin Hills, Los Angeles
66              Gallery Row, Los Angeles
67                 Garvanza, Los Angeles
68            Glassell Park, Los Angeles
69            Gramercy Park, Los Angeles
70            Granada Hills, Los Angeles
71            Green Meadows, Los Angeles
72                         Griffith Park
73             Hancock Park, Los Angeles
74              Harbor City, Los Angeles
75           Harbor Gateway, Los Angeles
76          Harvard Heights, Los Angeles
77             Harvard Park, Los Angeles
78                   Hermon, Los Angeles
79            Highland Park, Los Angeles
80            Historic Core, Los Angeles
81                             Hollywood
82           Hollywood Dell, Los Angeles
83                       Hollywood Hills
84     Hollywood Hills West, Los Angeles
85             Holmby Hills, Los Angeles
86                Hyde Park, Los Angeles
87           Jefferson Park, Los Angeles
88        Jewelry District (Los Angeles)
89           Kinney Heights, Los Angeles
90                Koreatown, Los Angeles
91                   Ladera, Los Angeles
92         Lafayette Square, Los Angeles
93              Lake Balboa, Los Angeles
94        Lake View Terrace, Los Angeles
95                Larchmont, Los Angeles
96            Laurel Canyon, Los Angeles
97        

In [9]:
# print the number of columns and rows of the dataframe
la_df.shape

(200, 1)

In [10]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Los Angeles, California'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [11]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in la_df["Neighborhood"].tolist() ]

In [12]:
# checking to see the latitude and longitude coordinates for the Los Angeles neighborhoods
coords

[[34.065136751126225, -118.25655551071065],
 [34.05539366680395, -118.23909786967798],
 [34.08758075672148, -118.26715413548087],
 [34.24905000000007, -118.43348999999995],
 [34.03989000000007, -118.32541999999995],
 [34.04807992671258, -118.2578500732874],
 [34.11970000000008, -118.25886999999994],
 [34.021570000000054, -118.36764999999997],
 [34.011569938831634, -118.33646000779022],
 [34.07044551895969, -118.2007101693803],
 [34.07044551895969, -118.2007101693803],
 [34.10915204015591, -118.32045343389233],
 [34.08361000000008, -118.43482999999998],
 [34.09384336187649, -118.42911274284965],
 [34.096529660177524, -118.4032980663708],
 [34.11793000000006, -118.44608999999997],
 [34.09544972015064, -118.42608605996772],
 [34.06151995614296, -118.39908997720605],
 [34.125234207116954, -118.41711206797373],
 [34.03866576497001, -118.3905079874249],
 [34.04004000000003, -118.21049999999997],
 [34.06626000000006, -118.47032999999999],
 [33.98805000000001, -118.277208],
 [33.98805000000001

In [13]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [14]:
# merge the coordinates into the original dataframe
la_df['Latitude'] = df_coords['Latitude']
la_df['Longitude'] = df_coords['Longitude']

In [15]:
# check the neighborhoods and the coordinates
print(la_df.shape)
la_df

(200, 3)


Neighborhood   Latitude   Longitude
0          Angelino Heights, Los Angeles  34.065137 -118.256556
1              Angeles Mesa, Los Angeles  34.055394 -118.239098
2             Angelus Vista, Los Angeles  34.087581 -118.267154
3                    Arleta, Los Angeles  34.249050 -118.433490
4         Arlington Heights, Los Angeles  34.039890 -118.325420
5             Arts District, Los Angeles  34.048080 -118.257850
6           Atwater Village, Los Angeles  34.119700 -118.258870
7             Baldwin Hills, Los Angeles  34.021570 -118.367650
8    Baldwin Hills/Crenshaw, Los Angeles  34.011570 -118.336460
9           Baldwin Village, Los Angeles  34.070446 -118.200710
10            Baldwin Vista, Los Angeles  34.070446 -118.200710
11         Beachwood Canyon, Los Angeles  34.109152 -118.320453
12                  Bel Air, Los Angeles  34.083610 -118.434830
13          Benedict Canyon, Los Angeles  34.093843 -118.429113
14            Beverly Crest, Los Angeles  34.096530 -118.403298
15             Beverly Glen, Los Angeles  34.117930 -118.446090
16            Beverly Grove, Los Angeles  34.095450 -118.426086
17             Beverly Hills Post Office  34.061520 -118.399090
18             Beverly Park, Los Angeles  34.125234 -118.417112
19              Beverlywood, Los Angeles  34.038666 -118.390508
20            Boyle Heights, Los Angeles  34.040040 -118.210500
21                Brentwood, Los Angeles  34.066260 -118.470330
22         Brentwood Circle, Los Angeles  33.988050 -118.277208
23           Brentwood Glen, Los Angeles  33.988050 -118.277208
24      Broadway-Manchester, Los Angeles  33.961030 -118.278310
25                Brookside, Los Angeles  34.113101 -118.477701
26              Bunker Hill, Los Angeles  34.063133 -118.244373
27                         Cahuenga Pass  34.124450 -118.342860
28              Canoga Park, Los Angeles  34.274200 -118.596440
29             Harvard Park, Los Angeles  33.844028 -118.306613
30                  Carthay, Los Angeles  34.053490 -118.245320
31           Castle Heights, Los Angeles  34.037934 -118.397492
32          Central-Alameda, Los Angeles  33.997420 -118.247780
33                  Downtown Los Angeles  34.048340 -118.255640
34             Century City, Los Angeles  34.059440 -118.412810
35               Chatsworth, Los Angeles  34.274392 -118.447862
36      Chesterfield Square, Los Angeles  33.992510 -118.312850
37            Cheviot Hills, Los Angeles  34.034030 -118.410560
38                Chinatown, Los Angeles  34.062290 -118.238370
39             Civic Center, Los Angeles  34.084140 -118.283390
40                 Crenshaw, Los Angeles  34.010710 -118.335120
41          Crestwood Hills, Los Angeles  34.130173 -118.191027
42             Cypress Park, Los Angeles  34.094480 -118.226780
43                  Del Rey, Los Angeles  33.988374 -118.445024
44                  Downtown Los Angeles  34.048340 -118.255640
45               Eagle Rock, Los Angeles  34.139270 -118.210870
46        East Gate Bel Air, Los Angeles  34.083610 -118.434830
47             Wikipedia:Citation needed  34.053490 -118.245320
48           East Hollywood, Los Angeles  34.090860 -118.293350
49          East Los Angeles, California  34.062340 -118.171590
50                Echo Park, Los Angeles  34.076090 -118.255810
51                 Edendale, Los Angeles  34.090680 -118.258480
52                El Sereno, Los Angeles  34.076850 -118.179340
53          Elysian Heights, Los Angeles  34.089050 -118.249300
54             Elysian Park, Los Angeles  34.082500 -118.233200
55           Elysian Valley, Los Angeles  34.094700 -118.240810
56                   Encino, Los Angeles  34.159607 -118.515485
57          Exposition Park, Los Angeles  34.011410 -118.290080
58        Faircrest Heights, Los Angeles  34.100184 -118.402452
59         Fairfax District, Los Angeles  34.076100 -118.361220
60         Fashion District, Los Angeles  34.037310 -118.252770
61    Historic Filipinotown, Los Angeles  34.053490 -118.245

In [16]:
# save the DataFrame as CSV file
la_df.to_csv("la_df.csv", index=False)

In [17]:
# get the coordinates of Los Angeles
address = 'Los Angeles, California USA'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpic coordinates of Los Angeles, California {}, {}.'.format(latitude, longitude))

The geograpic coordinates of Los Angeles, California 34.0536909, -118.2427666.


In [18]:
# create map of Los Angeles using latitude and longitude values 
map_la = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(la_df['Latitude'], la_df['Longitude'], la_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.5).add_to(map_la)  
    
map_la

In [19]:
# save the map as an HTML file
map_la.save('map_la.html')

### Using Foursquare to explore potential neighborhoods

In [20]:
# define Foursquare Credentials and Version
CLIENT_ID = '3JPMRUD4MLYIXAXGZSJJQQCHM2UE0DL4ZX2UMRN4ZHJBHMGW' # Foursquare ID
CLIENT_SECRET = 'WLU02ZN5BP1N0X40LUNCJFSXRAKOULETVD0QHF1PBDKSF5X2' # your Foursquare Secret
VERSION = '20200531' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3JPMRUD4MLYIXAXGZSJJQQCHM2UE0DL4ZX2UMRN4ZHJBHMGW
CLIENT_SECRET:WLU02ZN5BP1N0X40LUNCJFSXRAKOULETVD0QHF1PBDKSF5X2


In [21]:
radius = 2000
LIMIT = 200

venues = []

for lat, long, neighborhood in zip(la_df['Latitude'], la_df['Longitude'], la_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [22]:
# convert the venues list into a new data frame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(16840, 7)


Neighborhood   Latitude   Longitude  \
0  Angelino Heights, Los Angeles  34.065137 -118.256556   
1  Angelino Heights, Los Angeles  34.065137 -118.256556   
2  Angelino Heights, Los Angeles  34.065137 -118.256556   
3  Angelino Heights, Los Angeles  34.065137 -118.256556   
4  Angelino Heights, Los Angeles  34.065137 -118.256556   

                      VenueName  VenueLatitude  VenueLongitude   VenueCategory  
0            Vista Hermosa Park      34.061601     -118.256857            Park  
1             Pho Siam Thai Spa      34.066885     -118.260968  Massage Studio  
2                   Leo's Tacos      34.067743     -118.260974      Taco Place  
3  Bob Baker Marionette Theatre      34.061944     -118.259161         Theater  
4           Echo Park Deep Pool      34.064230     -118.259009            Pool

In [23]:
# determining how many venue categories are in the data frame
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  \
Neighborhood                                                          
Angeles Mesa, Los Angeles                 100        100        100   
Angelino Heights, Los Angeles             100        100        100   
Angelus Vista, Los Angeles                100        100        100   
Arleta, Los Angeles                        57         57         57   
Arlington Heights, Los Angeles            100        100        100   
Arts District, Los Angeles                100        100        100   
Atwater Village, Los Angeles              100        100        100   
Baldwin Hills, Los Angeles                 93         93         93   
Baldwin Hills/Crenshaw, Los Angeles        72         72         72   
Baldwin Village, Los Angeles               78         78         78   
Baldwin Vista, Los Angeles                 78         78         78   
Beachwood Canyon, Los Angeles             100        100        100   
Bel Air, Los Angeles                       68         68         68   
Benedict Canyon, Los Angeles               31         31         31   
Beverly Crest, Los Angeles                 45         45         45   
Beverly Glen, Los Angeles                  24         24         24   
Beverly Grove, Los Angeles                 24         24         24   
Beverly Hills Post Office                 100        100        100   
Beverly Park, Los Angeles                  12         12         12   
Beverlywood, Los Angeles                  100        100        100   
Boyle Heights, Los Angeles                100        100        100   
Brentwood Circle, Los Angeles              74         74         74   
Brentwood Glen, Los Angeles                74         74         74   
Brentwood, Los Angeles                    100        100        100   
Broadway-Manchester, Los Angeles           56         56         56   
Brookside, Los Angeles                     11         11         11   
Bunker Hill, Los Angeles                  100        100        100   
Cahuenga Pass                              82         82         82   
Canoga Park, Los Angeles                   32         32         32   
Carthay, Los Angeles                      100        100        100   
Castle Heights, Los Angeles               100        100        100   
Central-Alameda, Los Angeles               52         52         52   
Century City, Los Angeles                 100        100        100   
Chatsworth, Los Angeles                    78         78         78   
Chesterfield Square, Los Angeles           61         61         61   
Cheviot Hills, Los Angeles                100        100        100   
Chinatown, Los Angeles                    100        100        100   
Civic Center, Los Angeles                 100        100        100   
Crenshaw, Los Angeles                      69         69         69   
Crestwood Hills, Los Angeles              100        100        100   
Cypress Park, Los Angeles                  66         66         66   
Del Rey, Los Angeles                      100        100        100   
Downtown Los Angeles                      200        200        200   
Eagle Rock, Los Angeles                   100        100        100   
East Gate Bel Air, Los Angeles             68         68         68   
East Hollywood, Los Angeles               100        100        100   
East Los Angeles, California               42         42         42   
Echo Park, Los Angeles                    200        200        200   
Edendale, Los Angeles                     100        100        100   
El Sereno, Los Angeles                    110        110        110   
Elysian Heights, Los Angeles              100        100        100   
Elysian Park, Los Angeles                 100        100        100   
Elysian Valley, Los Angeles                92         92         92   
Encino, Los Angeles                       100        100        100   
Exposition Park, Los Angeles              100        100     

In [24]:
# printing the number of unique categories
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 414 uniques categories.


In [25]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:50]

array(['Park', 'Massage Studio', 'Taco Place', 'Theater', 'Pool',
       'Performing Arts Venue', 'Bar', 'Coffee Shop', 'Deli / Bodega',
       'Cocktail Bar', 'Music Venue', 'Plaza', 'American Restaurant',
       'Concert Hall', 'Arcade', 'Japanese Restaurant', 'Sake Bar',
       'Convenience Store', 'Art Gallery', 'Art Museum', 'Beer Store',
       'Vegetarian / Vegan Restaurant', 'Pizza Place', 'Café',
       'Latin American Restaurant', 'Breakfast Spot', 'School',
       'Pet Store', 'Wine Bar', 'Bookstore', 'Museum', 'Library',
       'Lounge', 'Gastropub', 'Gym / Fitness Center', 'Rock Club',
       'Bakery', 'Circus', 'Speakeasy', 'Motel', 'Filipino Restaurant',
       'Baseball Stadium', 'Ice Cream Shop', 'General Entertainment',
       'Market', 'Health Food Store', 'Fried Chicken Joint',
       'Mexican Restaurant', 'Fast Food Restaurant', 'Gym'], dtype=object)

In [26]:
# check if the results contain "Art Gallery"
"Neighborhood" in venues_df['VenueCategory'].unique()

True

### Analyze each neighborhood

In [27]:
# one hot encoding
la_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
la_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [la_onehot.columns[-1]] + list(la_onehot.columns[:-1])
la_onehot = la_onehot[fixed_columns]

print(la_onehot.shape)
la_onehot.head()

(16840, 415)


Neighborhoods  ATM  Accessories Store  Adult Boutique  \
0  Angelino Heights, Los Angeles    0                  0               0   
1  Angelino Heights, Los Angeles    0                  0               0   
2  Angelino Heights, Los Angeles    0                  0               0   
3  Angelino Heights, Los Angeles    0                  0               0   
4  Angelino Heights, Los Angeles    0                  0               0   

   Airport  Airport Lounge  Airport Service  American Restaurant  \
0        0               0                0                    0   
1        0               0                0                    0   
2        0               0                0                    0   
3        0               0                0                    0   
4        0               0                0                    0   

   Amphitheater  Antique Shop  Aquarium  Arcade  Argentinian Restaurant  \
0             0             0         0       0                       0   
1             0             0         0       0                       0   
2             0             0         0       0                       0   
3             0             0         0       0                       0   
4             0             0         0       0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  Astrologer  \
0            0           0                    0                 0           0   
1            0           0                    0                 0           0   
2            0           0                    0                 0           0   
3            0           0                    0                 0           0   
4            0           0                    0                 0           0   

   Athletics & Sports  Australian Restaurant  Auto Dealership  Auto Garage  \
0                   0                      0                0            0   
1                   0                      0                0            0   
2                   0                      0                0            0   
3                   0                      0                0            0   
4                   0                      0                0            0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                0         0            0           0              0   
1                0         0            0           0              0   
2                0         0            0           0              0   
3                0         0            0           0              0   
4                0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0   

In [28]:
# creating a new data frame consisting of neighborhood and venue data 
la_grouped = la_onehot.groupby(["Neighborhoods"]).mean().reset_index()

# checking the shape of the new data frame
print(la_grouped.shape)

# checking the new data frame
la_grouped

(191, 415)


Neighborhoods       ATM  Accessories Store  \
0              Angeles Mesa, Los Angeles  0.000000           0.000000   
1          Angelino Heights, Los Angeles  0.000000           0.000000   
2             Angelus Vista, Los Angeles  0.000000           0.010000   
3                    Arleta, Los Angeles  0.000000           0.000000   
4         Arlington Heights, Los Angeles  0.000000           0.000000   
5             Arts District, Los Angeles  0.000000           0.000000   
6           Atwater Village, Los Angeles  0.010000           0.000000   
7             Baldwin Hills, Los Angeles  0.000000           0.000000   
8    Baldwin Hills/Crenshaw, Los Angeles  0.000000           0.013889   
9           Baldwin Village, Los Angeles  0.000000           0.000000   
10            Baldwin Vista, Los Angeles  0.000000           0.000000   
11         Beachwood Canyon, Los Angeles  0.000000           0.000000   
12                  Bel Air, Los Angeles  0.000000           0.000000   
13          Benedict Canyon, Los Angeles  0.000000           0.000000   
14            Beverly Crest, Los Angeles  0.000000           0.000000   
15             Beverly Glen, Los Angeles  0.000000           0.000000   
16            Beverly Grove, Los Angeles  0.000000           0.000000   
17             Beverly Hills Post Office  0.000000           0.000000   
18             Beverly Park, Los Angeles  0.000000           0.000000   
19              Beverlywood, Los Angeles  0.000000           0.000000   
20            Boyle Heights, Los Angeles  0.010000           0.000000   
21         Brentwood Circle, Los Angeles  0.000000           0.000000   
22           Brentwood Glen, Los Angeles  0.000000           0.000000   
23                Brentwood, Los Angeles  0.000000           0.000000   
24      Broadway-Manchester, Los Angeles  0.000000           0.000000   
25                Brookside, Los Angeles  0.000000           0.000000   
26              Bunker Hill, Los Angeles  0.000000           0.000000   
27                         Cahuenga Pass  0.000000           0.000000   
28              Canoga Park, Los Angeles  0.000000           0.000000   
29                  Carthay, Los Angeles  0.000000           0.000000   
30           Castle Heights, Los Angeles  0.000000           0.000000   
31          Central-Alameda, Los Angeles  0.000000           0.000000   
32             Century City, Los Angeles  0.000000           0.000000   
33               Chatsworth, Los Angeles  0.000000           0.000000   
34      Chesterfield Square, Los Angeles  0.016393           0.000000   
35            Cheviot Hills, Los Angeles  0.000000           0.000000   
36                Chinatown, Los Angeles  0.000000           0.000000   
37             Civic Center, Los Angeles  0.000000           0.010000   
38                 Crenshaw, Los Angeles  0.000000           0.014493   
39          Crestwood Hills, Los Angeles  0.000000           0.000000   
40             Cypress Park, Los Angeles  0.000000           0.000000   
41                  Del Rey, Los Angeles  0.000000           0.000000   
42                  Downtown Los Angeles  0.000000           0.000000   
43               Eagle Rock, Los Angeles  0.000000           0.000000   
44        East Gate Bel Air, Los Angeles  0.000000           0.000000   
45           East Hollywood, Los Angeles  0.000000           0.000000   
46          East Los Angeles, California  0.000000           0.000000   
47                Echo Park, Los Angeles  0.000000           0.000000   
48                 Edendale, Los Angeles  0.000000           0.000000   
49                El Sereno, Los Angeles  0.018182           0.000000   
50          Elysian Heights, Los Angeles  0.000000           0.000000   
51             Elysian Park, Los Angeles  0.000000           0.000000   
52           Elysian Valley, Los Angeles  0.010870           0.000000   
53                   Encino, Los Angeles  0.000000           0.000000   
54          

In [29]:
# check to see how many art galleries are in Los Angeles neighborhoods
len(la_grouped[la_grouped["Art Gallery"] > 0])

79

### Create a new data frame with art gallery frequency and neighborhood location data

In [30]:
# creating a new data frame of neighborhood and art gallery information
la_gallery = la_grouped[["Neighborhoods", "Art Gallery"]]

In [31]:
# checking to see the new data frame
la_gallery.head()

Neighborhoods  Art Gallery
0       Angeles Mesa, Los Angeles         0.03
1   Angelino Heights, Los Angeles         0.02
2      Angelus Vista, Los Angeles         0.01
3             Arleta, Los Angeles         0.00
4  Arlington Heights, Los Angeles         0.01

In [32]:
# galleries in Los Angeles
la_gallery

Neighborhoods  Art Gallery
0              Angeles Mesa, Los Angeles     0.030000
1          Angelino Heights, Los Angeles     0.020000
2             Angelus Vista, Los Angeles     0.010000
3                    Arleta, Los Angeles     0.000000
4         Arlington Heights, Los Angeles     0.010000
5             Arts District, Los Angeles     0.010000
6           Atwater Village, Los Angeles     0.000000
7             Baldwin Hills, Los Angeles     0.032258
8    Baldwin Hills/Crenshaw, Los Angeles     0.000000
9           Baldwin Village, Los Angeles     0.012821
10            Baldwin Vista, Los Angeles     0.012821
11         Beachwood Canyon, Los Angeles     0.000000
12                  Bel Air, Los Angeles     0.000000
13          Benedict Canyon, Los Angeles     0.000000
14            Beverly Crest, Los Angeles     0.000000
15             Beverly Glen, Los Angeles     0.000000
16            Beverly Grove, Los Angeles     0.000000
17             Beverly Hills Post Office     0.020000
18             Beverly Park, Los Angeles     0.000000
19              Beverlywood, Los Angeles     0.040000
20            Boyle Heights, Los Angeles     0.030000
21         Brentwood Circle, Los Angeles     0.000000
22           Brentwood Glen, Los Angeles     0.000000
23                Brentwood, Los Angeles     0.050000
24      Broadway-Manchester, Los Angeles     0.000000
25                Brookside, Los Angeles     0.000000
26              Bunker Hill, Los Angeles     0.020000
27                         Cahuenga Pass     0.000000
28              Canoga Park, Los Angeles     0.000000
29                  Carthay, Los Angeles     0.020000
30           Castle Heights, Los Angeles     0.010000
31          Central-Alameda, Los Angeles     0.000000
32             Century City, Los Angeles     0.020000
33               Chatsworth, Los Angeles     0.000000
34      Chesterfield Square, Los Angeles     0.000000
35            Cheviot Hills, Los Angeles     0.000000
36                Chinatown, Los Angeles     0.030000
37             Civic Center, Los Angeles     0.000000
38                 Crenshaw, Los Angeles     0.000000
39          Crestwood Hills, Los Angeles     0.020000
40             Cypress Park, Los Angeles     0.015152
41                  Del Rey, Los Angeles     0.000000
42                  Downtown Los Angeles     0.000000
43               Eagle Rock, Los Angeles     0.010000
44        East Gate Bel Air, Los Angeles     0.000000
45           East Hollywood, Los Angeles     0.000000
46          East Los Angeles, California     0.000000
47                Echo Park, Los Angeles     0.020000
48                 Edendale, Los Angeles     0.010000
49                El Sereno, Los Angeles     0.000000
50          Elysian Heights, Los Angeles     0.020000
51             Elysian Park, Los Angeles     0.040000
52           Elysian Valley, Los Angeles     0.010870
53                   Encino, Los Angeles     0.000000
54          Exposition Park, Los Angeles     0.000000
55        Faircrest Heights, Los Angeles     0.000000
56         Fairfax District, Los Angeles     0.010000
57         Fashion District, Los Angeles     0.010000
58       Financial District, Los Angeles     0.010000
59                 Florence, Los Angeles     0.000000
60           Franklin Hills, Los Angeles     0.000000
61              Gallery Row, Los Angeles     0.000000
62                 Garvanza, Los Angeles     0.013889
63            Glassell Park, Los Angeles     0.000000
64            Gramercy Park, Los Angeles     0.010417
65            Granada Hills, Los Angeles     0.000000
66            Green Meadows, Los Angeles     0.000000
67                         Griffith Park     0.000000
68             Hancock Park, Los Angeles     0.000000
69              Harbor City, Los Angeles     0.000000
70           Harbor Gateway, Los Angeles     0.000000
71          Harvard Heights, Los Angeles     0.010000
72             Harvard Park, Los Angeles     0.000000
73                   Hermon, Lo

### Cluster neighborhoods using k-means

In [33]:
# set number of clusters
laclusters = 3

la_clustering = la_gallery.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=laclusters, random_state=0).fit(la_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 0, 0, 2, 0, 0, 2, 1, 2, 0])

In [34]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
la_merged = la_gallery.copy()

# add clustering labels
la_merged["Cluster Labels"] = kmeans.labels_

In [35]:
la_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
la_merged.head()

Neighborhood  Art Gallery  Cluster Labels
0       Angeles Mesa, Los Angeles         0.03               1
1   Angelino Heights, Los Angeles         0.02               0
2      Angelus Vista, Los Angeles         0.01               0
3             Arleta, Los Angeles         0.00               2
4  Arlington Heights, Los Angeles         0.01               0

In [36]:
# merge la_grouped with la_data to add latitude/longitude for each neighborhood
la_merged = la_merged.join(la_df.set_index("Neighborhood"), on="Neighborhood")

print(la_merged.shape)
la_merged.head() # check the last columns!


(200, 5)


Neighborhood  Art Gallery  Cluster Labels   Latitude  \
0       Angeles Mesa, Los Angeles         0.03               1  34.055394   
1   Angelino Heights, Los Angeles         0.02               0  34.065137   
2      Angelus Vista, Los Angeles         0.01               0  34.087581   
3             Arleta, Los Angeles         0.00               2  34.249050   
4  Arlington Heights, Los Angeles         0.01               0  34.039890   

    Longitude  
0 -118.239098  
1 -118.256556  
2 -118.267154  
3 -118.433490  
4 -118.325420

In [37]:
# sort the results by Cluster Labels
print(la_merged.shape)
la_merged.sort_values(["Cluster Labels"], inplace=True)
la_merged

(200, 5)


Neighborhood  Art Gallery  Cluster Labels  \
115      NoHo Arts District, Los Angeles     0.010000               0   
73                   Hermon, Los Angeles     0.020833               0   
39          Crestwood Hills, Los Angeles     0.020000               0   
40             Cypress Park, Los Angeles     0.015152               0   
110       Montecito Heights, Los Angeles     0.018182               0   
108            Miracle Mile, Los Angeles     0.010000               0   
107            Mid-Wilshire, Los Angeles     0.010000               0   
43               Eagle Rock, Los Angeles     0.010000               0   
106                Mid-City, Los Angeles     0.010000               0   
105            Melrose Hill, Los Angeles     0.010000               0   
47                Echo Park, Los Angeles     0.020000               0   
47                Echo Park, Los Angeles     0.020000               0   
48                 Edendale, Los Angeles     0.010000               0   
97          Little Ethiopia, Los Angeles     0.020000               0   
50          Elysian Heights, Los Angeles     0.020000               0   
189          Woodland Hills, Los Angeles     0.010000               0   
52           Elysian Valley, Los Angeles     0.010870               0   
90              Lake Balboa, Los Angeles     0.010000               0   
75            Historic Core, Los Angeles     0.020000               0   
76    Historic Filipinotown, Los Angeles     0.020000               0   
77    Historic South Central Los Angeles     0.011236               0   
79           Hollywood Dell, Los Angeles     0.010000               0   
64            Gramercy Park, Los Angeles     0.010417               0   
82             Holmby Hills, Los Angeles     0.010000               0   
116             North Hills, Los Angeles     0.010000               0   
62                 Garvanza, Los Angeles     0.013889               0   
85        Jewelry District (Los Angeles)     0.010000               0   
86           Kinney Heights, Los Angeles     0.010870               0   
58       Financial District, Los Angeles     0.010000               0   
57         Fashion District, Los Angeles     0.010000               0   
56         Fairfax District, Los Angeles     0.010000               0   
89         Lafayette Square, Los Angeles     0.020000               0   
84           Jefferson Park, Los Angeles     0.011364               0   
120       Old Bank District, Los Angeles     0.010000               0   
71          Harvard Heights, Los Angeles     0.010000               0   
17             Beverly Hills Post Office     0.020000               0   
180                Westwood, Los Angeles     0.010000               0   
179        Westwood Village, Los Angeles     0.010000               0   
176                Westdale, Los Angeles     0.010000               0   
174                     West Los Angeles     0.010000               0   
168           Victoria Park, Los Angeles     0.020000               0   
126            Park La Brea, Los Angeles     0.010000               0   
183            Wikipedia:Citation needed     0.020000               0   
161          Valley Village, Los Angeles     0.012500               0   
5             Arts District, Los Angeles     0.010000               0   
158            Toy District, Los Angeles     0.010000               0   
10            Baldwin Vista, Los Angeles     0.012821               0   
183            Wikipedia:Citation needed     0.020000               0   
4         Arlington Heights, Los Angeles     0.010000               0   
144                Skid Row, Los Angeles     0.020000               0   
143             Silver Lake, Los Angeles     0.010000               0   
139                Sawtelle, Los Angeles     0.010000               0   
26              Bunker Hill, Los Angeles     0.020000               0   
1          Angelino Heights, Los Angeles     0.020000               0   
133          

### Visualise the clusters

In [38]:
# create a map of the clusters

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(laclusters)
ys = [i+x+(i*x)**2 for i in range(laclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(la_merged['Latitude'], la_merged['Longitude'], la_merged['Neighborhood'], la_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [39]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

### Check clusters

In [40]:
la_merged.loc[la_merged['Cluster Labels'] == 0]

Neighborhood  Art Gallery  Cluster Labels  \
115     NoHo Arts District, Los Angeles     0.010000               0   
73                  Hermon, Los Angeles     0.020833               0   
39         Crestwood Hills, Los Angeles     0.020000               0   
40            Cypress Park, Los Angeles     0.015152               0   
110      Montecito Heights, Los Angeles     0.018182               0   
108           Miracle Mile, Los Angeles     0.010000               0   
107           Mid-Wilshire, Los Angeles     0.010000               0   
43              Eagle Rock, Los Angeles     0.010000               0   
106               Mid-City, Los Angeles     0.010000               0   
105           Melrose Hill, Los Angeles     0.010000               0   
47               Echo Park, Los Angeles     0.020000               0   
47               Echo Park, Los Angeles     0.020000               0   
48                Edendale, Los Angeles     0.010000               0   
97         Little Ethiopia, Los Angeles     0.020000               0   
50         Elysian Heights, Los Angeles     0.020000               0   
189         Woodland Hills, Los Angeles     0.010000               0   
52          Elysian Valley, Los Angeles     0.010870               0   
90             Lake Balboa, Los Angeles     0.010000               0   
75           Historic Core, Los Angeles     0.020000               0   
76   Historic Filipinotown, Los Angeles     0.020000               0   
77   Historic South Central Los Angeles     0.011236               0   
79          Hollywood Dell, Los Angeles     0.010000               0   
64           Gramercy Park, Los Angeles     0.010417               0   
82            Holmby Hills, Los Angeles     0.010000               0   
116            North Hills, Los Angeles     0.010000               0   
62                Garvanza, Los Angeles     0.013889               0   
85       Jewelry District (Los Angeles)     0.010000               0   
86          Kinney Heights, Los Angeles     0.010870               0   
58      Financial District, Los Angeles     0.010000               0   
57        Fashion District, Los Angeles     0.010000               0   
56        Fairfax District, Los Angeles     0.010000               0   
89        Lafayette Square, Los Angeles     0.020000               0   
84          Jefferson Park, Los Angeles     0.011364               0   
120      Old Bank District, Los Angeles     0.010000               0   
71         Harvard Heights, Los Angeles     0.010000               0   
17            Beverly Hills Post Office     0.020000               0   
180               Westwood, Los Angeles     0.010000               0   
179       Westwood Village, Los Angeles     0.010000               0   
176               Westdale, Los Angeles     0.010000               0   
174                    West Los Angeles     0.010000               0   
168          Victoria Park, Los Angeles     0.020000               0   
126           Park La Brea, Los Angeles     0.010000               0   
183           Wikipedia:Citation needed     0.020000               0   
161         Valley Village, Los Angeles     0.012500               0   
5            Arts District, Los Angeles     0.010000               0   
158           Toy District, Los Angeles     0.010000               0   
10           Baldwin Vista, Los Angeles     0.012821               0   
183           Wikipedia:Citation needed     0.020000               0   
4        Arlington Heights, Los Angeles     0.010000               0   
144               Skid Row, Los Angeles     0.020000               0   
143            Silver Lake, Los Angeles     0.010000               0   
139               Sawtelle, Los Angeles     0.010000               0   
26             Bunker Hill, Los Angeles     0.020000               0   
1         Angelino Heights, Los Angeles     0.020000               0   
133            Rancho Park, Los Angeles     0.010000               

In [41]:
la_merged.loc[la_merged['Cluster Labels'] == 1]

Neighborhood  Art Gallery  Cluster Labels   Latitude  \
182  Wholesale District, Los Angeles     0.050000               1  34.036706   
182  Wholesale District, Los Angeles     0.050000               1  34.036706   
74        Highland Park, Los Angeles     0.030000               1  34.109820   
127     Picfair Village, Los Angeles     0.030000               1  34.045000   
92            Larchmont, Los Angeles     0.030000               1  34.080990   
163              Venice, Los Angeles     0.040000               1  34.038157   
98         Little Tokyo, Los Angeles     0.040000               1  34.048310   
147     South Robertson, Los Angeles     0.040000               1  34.046520   
145       Solano Canyon, Los Angeles     0.040000               1  34.082035   
99       Los Angeles Flower District     0.030000               1  34.056960   
135     Reynier Village, Los Angeles     0.040000               1  34.035874   
113    Mount Washington, Los Angeles     0.027027               1  34.099040   
169       Village Green, Los Angeles     0.040541               1  34.019938   
0          Angeles Mesa, Los Angeles     0.030000               1  34.055394   
95      Lincoln Heights, Los Angeles     0.037975               1  34.069830   
19          Beverlywood, Los Angeles     0.040000               1  34.038666   
20        Boyle Heights, Los Angeles     0.030000               1  34.040040   
51         Elysian Park, Los Angeles     0.040000               1  34.082500   
7         Baldwin Hills, Los Angeles     0.032258               1  34.021570   
23            Brentwood, Los Angeles     0.050000               1  34.066260   
36            Chinatown, Los Angeles     0.030000               1  34.062290   

      Longitude  
182 -118.236463  
182 -118.236463  
74  -118.192320  
127 -118.365280  
92  -118.323650  
163 -118.372921  
98  -118.236190  
147 -118.386170  
145 -118.234983  
99  -118.240070  
135 -118.385956  
113 -118.211340  
169 -118.365432  
0   -118.239098  
95  -118.211640  
19  -118.390508  
20  -118.210500  
51  -118.233200  
7   -118.367650  
23  -118.470330  
36  -118.238370

In [42]:
la_merged.loc[la_merged['Cluster Labels'] == 2]

Neighborhood  Art Gallery  Cluster Labels  \
159         University Park, Los Angeles          0.0               2   
157             Toluca Lake, Los Angeles          0.0               2   
156               Thai Town, Los Angeles          0.0               2   
155                      Terminal Island          0.0               2   
154                 Tarzana, Los Angeles          0.0               2   
153                  Sylmar, Los Angeles          0.0               2   
152         Sunset Junction, Los Angeles          0.0               2   
151         Sunland-Tujunga, Los Angeles          0.0               2   
151         Sunland-Tujunga, Los Angeles          0.0               2   
150              Sun Valley, Los Angeles          0.0               2   
72             Harvard Park, Los Angeles          0.0               2   
148        Spaulding Square, Los Angeles          0.0               2   
21         Brentwood Circle, Los Angeles          0.0               2   
146              South Park, Los Angeles          0.0               2   
22           Brentwood Glen, Los Angeles          0.0               2   
24      Broadway-Manchester, Los Angeles          0.0               2   
142         Sherman Village, Los Angeles          0.0               2   
141            Sherman Oaks, Los Angeles          0.0               2   
140            Shadow Hills, Los Angeles          0.0               2   
25                Brookside, Los Angeles          0.0               2   
138               San Pedro, Los Angeles          0.0               2   
137           Rustic Canyon, Los Angeles          0.0               2   
136              Rose Hills, Los Angeles          0.0               2   
160             Valley Glen, Los Angeles          0.0               2   
149             Studio City, Los Angeles          0.0               2   
18             Beverly Park, Los Angeles          0.0               2   
27                         Cahuenga Pass          0.0               2   
188                Winnetka, Los Angeles          0.0               2   
187          Windsor Square, Los Angeles          0.0               2   
186           Wilshire Park, Los Angeles          0.0               2   
185         Wilshire Center, Los Angeles          0.0               2   
184              Wilmington, Los Angeles          0.0               2   
3                    Arleta, Los Angeles          0.0               2   
6           Atwater Village, Los Angeles          0.0               2   
8    Baldwin Hills/Crenshaw, Los Angeles          0.0               2   
181         Whitley Heights, Los Angeles          0.0               2   
11         Beachwood Canyon, Los Angeles          0.0               2   
12                  Bel Air, Los Angeles          0.0               2   
178        Westside Village, Los Angeles          0.0               2   
177                Westlake, Los Angeles          0.0               2   
13          Benedict Canyon, Los Angeles          0.0               2   
175             Westchester, Los Angeles          0.0               2   
14            Beverly Crest, Los Angeles          0.0               2   
173              West Hills, Los Angeles          0.0               2   
172              West Adams, Los Angeles          0.0               2   
172              West Adams, Los Angeles          0.0               2   
171                   Watts, Los Angeles          0.0               2   
170           Warner Center, Los Angeles          0.0               2   
15             Beverly Glen, Los Angeles          0.0               2   
16            Beverly Grove, Los Angeles          0.0               2   
167         Vermont-Slauson, Los Angeles          0.0               2   
166           Vermont Vista, Los Angeles          0.0               2   
165          Vermont Square, Los Angeles          0.0               2   
164          Vermont Knolls, Los Angeles          0.0               2   
162          

## Results

The results of this project further reveal the complexity and challenge of locating a new art gallery in Los Angeles. That is, there are 200 neighborhoods in Los Angeles, with 415 unique venues within a 2,000 meter radius of their locations, including a total of 79 existing art galleries. From these neighborhoods, this project has identified a number of potential neighborhoods to locate a new art gallery using k-means clustering.


## Discussion and Observations

Los Angeles has a population of 4 million people, living in 200 different neighborhoods, exacerbated by its transportation system, and far-flung development. The long-time trend of building out, versus up, and using freeways as opposed to a robust public transportation system, has created world-class urban sprawl for Los Angeles residents. Selecting a specific location for an art gallery is extremely challenging under these conditions. This study has helped identify potential locations in Cluster 1 neighborhoods, based on the current locations of existing galleries. 

## Conclusion

Further analysis is encouraged to narrow down specific locations in Cluster 1 neighborhoods. Neighborhoods that show particular promise include: Chinatown, Los Angeles Flower District, and the Little Tokyo/Arts District. These are all located in the Downtown Los Angeles area, but slightly to the southeast of the Los Angeles Civic Center.